In [114]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import seaborn as sns
%matplotlib
import re
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize 
from xgboost import XGBClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import accuracy_score
from sklearn.tree import DecisionTreeClassifier
from keras.callbacks import EarlyStopping
import math
import os
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.metrics.pairwise import linear_kernel, cosine_similarity
from nltk.stem.snowball import SnowballStemmer
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer

Using matplotlib backend: Qt5Agg


Using TensorFlow backend.


In [2]:
path="D:/scrapping/magicbricks/"
df=pd.read_csv(f'{path}data_gnr_jan.csv')

In [3]:
df.head()

Unnamed: 0                    Society     addressLocality  \
0           0  Golfforeste AC Apartments              Zeta 1   
1           1            SKA Metro Ville          Eta 2, Eta   
2           2                Prideville    Yamuna Expressway   
3           3      Purvanchal Royal City               Chi 5   
4           4                Stellar One  Greater Noida West   

                agentCompanyName agentMaskedmobilenumber  \
0        BD Green Home Pvt. Ltd.         +91-88XXXXXXX90   
1                            NaN         +91-91XXXXXXX15   
2        Imperia Structures Ltd.         +91-74XXXXXXX93   
3  Purvanchal Projects Pvt. Ltd.         +91-78XXXXXXX42   
4     Stellar Ventures Pvt. Ltd.         +91-98XXXXXXX77   

                    agentName  bathroom  bedroom  \
0           Praveen Choudhary       2.0      2.0   
1                   SKA GROUP       2.0      2.0   
2                       Vipin       2.0      2.0   
3              Shashi  Kapoor       4.0      4.0   
4  Stellar Ventures Pvt. Ltd.       2.0      2.0   

                     builderName       cityName  ...            locality  \
0                Paramount Group  Greater Noida  ...              Zeta 1   
1                      SKA Group  Greater Noida  ...          Eta 2, Eta   
2        Imperia Structures Ltd.  Greater Noida  ...   Yamuna Expressway   
3  Purvanchal Projects Pvt. Ltd.  Greater Noida  ...               Chi 5   
4     Stellar Ventures Pvt. Ltd.  Greater Noida  ...  Greater Noida West   

   longitude                                               name numberOfRooms  \
0        NaN  2 BHK Apartment for Sale in Golfforeste AC Apa...           2.0   
1  28.496992  2 BHK Apartment for Sale in SKA Metro Ville, E...           2.0   
2        NaN  2 BHK Apartment for Sale in Prideville , Yamun...           2.0   
3  28.430194  4 BHK Apartment for Sale in Purvanchal Royal C...           4.0   
4  28.576390  2 BHK Apartment for Sale in Stellar One, Great...           2.0   

  postedBy       price  priceInWord                projectName  propertyType  \
0    Agent   3710000.0     37.1 Lac  Golfforeste AC Apartments     Apartment   
1  Builder   2560000.0     25.6 Lac            SKA Metro Ville     Apartment   
2  Builder   4680000.0     46.8 Lac                Prideville      Apartment   
3  Builder  11200000.0      1.12 Cr      Purvanchal Royal City     Apartment   
4  Builder   3110000.0     31.1 Lac                Stellar One     Apartment   

                                                 url  
0  https://www.magicbricks.com/propertyDetails/2-...  
1  https://www.magicbricks.com/propertyDetails/2-...  
2  https://www.magicbricks.com/propertyDetails/2-...  
3  https://www.magicbricks.com/propertyDetails/4-...  
4  https://www.magicbricks.com/propertyDetails/2-...  

[5 rows x 27 columns]

In [4]:
df.columns

Index(['Unnamed: 0', 'Society', 'addressLocality', 'agentCompanyName',
       'agentMaskedmobilenumber', 'agentName', 'bathroom', 'bedroom',
       'builderName', 'cityName', 'createdDate', 'description', 'floorSize',
       'floorno', 'furnshingstatus', 'id', 'latitude', 'locality', 'longitude',
       'name', 'numberOfRooms', 'postedBy', 'price', 'priceInWord',
       'projectName', 'propertyType', 'url'],
      dtype='object')

In [5]:
df.description.unique()[0]

'2 Bath,Unfurnished,16 floor Paramount Golf Forest Ac Apartments complimented by designer landscape with a green golf course for you and your family, a well-deserved healthy lifestyle.'

In [6]:
df.name.unique()[0]

'2 BHK Apartment for Sale in Golfforeste AC Apartments, Zeta 1'

In [7]:
df.locality[0]

'Zeta 1'

In [8]:
df.locality.nunique()

106

In [9]:
df.shape

(1555, 27)

In [13]:
df['createdDate']=pd.to_datetime(df['createdDate'])

In [11]:
def null_values(DataFrame_Name):
    
    sum_null = DataFrame_Name.isnull().sum()
    total_count = DataFrame_Name.isnull().count()
    percent_nullvalues = sum_null/total_count * 100
    df_null = pd.DataFrame()
    df_null['Total_values'] = total_count
    df_null['Null_Count'] = sum_null
    df_null['Percent'] = percent_nullvalues
    df_null = df_null.sort_values(by='Null_Count',ascending = False)

    return(df_null)

In [41]:
df=df[~df.furnshingstatus.isnull()]

In [42]:
null_values(df)

Total_values  Null_Count    Percent
agentCompanyName                  734         567  77.247956
longitude                         734          28   3.814714
latitude                          734          28   3.814714
Unnamed: 0                        734           0   0.000000
furnshingstatus                   734           0   0.000000
propertyType                      734           0   0.000000
projectName                       734           0   0.000000
priceInWord                       734           0   0.000000
price                             734           0   0.000000
postedBy                          734           0   0.000000
numberOfRooms                     734           0   0.000000
name                              734           0   0.000000
locality                          734           0   0.000000
id                                734           0   0.000000
floorno                           734           0   0.000000
Society                           734           0   0.000000
floorSize                         734           0   0.000000
description                       734           0   0.000000
createdDate                       734           0   0.000000
cityName                          734           0   0.000000
builderName                       734           0   0.000000
bedroom                           734           0   0.000000
bathroom                          734           0   0.000000
agentName                         734           0   0.000000
agentMaskedmobilenumber           734           0   0.000000
addressLocality                   734           0   0.000000
url                               734           0   0.000000

In [40]:
df[df['furnshingstatus'].isnull()]

Unnamed: 0                 Society addressLocality agentCompanyName  \
668         668  Plumeria Garden Estate       Omicron 3              NaN   

    agentMaskedmobilenumber        agentName  bathroom  bedroom  \
668         +91-98XXXXXXX86  Abhishek Chopra       3.0      4.0   

            builderName       cityName  ...   locality  longitude  \
668  Uppal Chadha Group  Greater Noida  ...  Omicron 3  28.475161   

                                                  name numberOfRooms postedBy  \
668  4 BHK Apartment for Sale in Plumeria Garden Es...           4.0    Owner   

       price  priceInWord             projectName  propertyType  \
668  7.5e+06       75 Lac  Plumeria Garden Estate     Apartment   

                                                   url  
668  https://www.magicbricks.com/propertyDetails/4-...  

[1 rows x 27 columns]

In [24]:
df.projectName.fillna('Not available',inplace=True)

In [21]:
df.floorno.fillna('Not available',inplace=True)

In [22]:
df.price.fillna('Not define',inplace=True)

In [16]:
def replace_ftk(x):
    #print(x)
    if(re.findall(r'FTK',x)):
        result = re.sub(r'FTK','',x)
    else:
        result = x
    return (result)

In [14]:
df.head().T

0  \
Unnamed: 0                                                               0   
Society                                          Golfforeste AC Apartments   
addressLocality                                                     Zeta 1   
agentCompanyName                                   BD Green Home Pvt. Ltd.   
agentMaskedmobilenumber                                    +91-88XXXXXXX90   
agentName                                                Praveen Choudhary   
bathroom                                                                 2   
bedroom                                                                  2   
builderName                                                Paramount Group   
cityName                                                     Greater Noida   
createdDate                                  1970-01-01 00:00:00.020200128   
description              2 Bath,Unfurnished,16 floor Paramount Golf For...   
floorSize                                                        1260 FTK    
floorno                                                                 16   
furnshingstatus                                                Unfurnished   
id                                                   domcache_srp_46630105   
latitude                                                               NaN   
locality                                                            Zeta 1   
longitude                                                              NaN   
name                     2 BHK Apartment for Sale in Golfforeste AC Apa...   
numberOfRooms                                                            2   
postedBy                                                             Agent   
price                                                             3.71e+06   
priceInWord                                                       37.1 Lac   
projectName                                      Golfforeste AC Apartments   
propertyType                                                     Apartment   
url                      https://www.magicbricks.com/propertyDetails/2-...   

                                                                         1  \
Unnamed: 0                                                               1   
Society                                                    SKA Metro Ville   
addressLocality                                                 Eta 2, Eta   
agentCompanyName                                                       NaN   
agentMaskedmobilenumber                                    +91-91XXXXXXX15   
agentName                                                        SKA GROUP   
bathroom                                                                 2   
bedroom                                                                  2   
builderName                                                      SKA Group   
cityName                                                     Greater Noida   
createdDate                                  1970-01-01 00:00:00.020200128   
description              2 Bath,Semi-Furnished SKA Metro Ville is the f...   
floorSize                                                         920 FTK    
floorno                                                                NaN   
furnshingstatus                                             Semi-Furnished   
id                                                   domcache_srp_46365021   
latitude                                                           77.5375   
locality                                                        Eta 2, Eta   
longitude                                                           28.497   
name                     2 BHK Apartment for Sale in SKA Metro Ville, E...   
numberOfRooms                                                            2   
postedBy                                                           Builder   
price                                                             2.56e+06   
priceInWord     

In [17]:
df['floorSize']=df.floorSize.apply(lambda x : replace_ftk(str(x)))

In [148]:
df_recommend=df[['Society', 'locality', 'bathroom', 'bedroom',
       'builderName', 'cityName','floorSize',
       'floorno', 'furnshingstatus','name','price', 'priceInWord', 'propertyType','name','description']]

In [149]:
df_recommend.head()

Society            locality  bathroom  bedroom  \
0  Golfforeste AC Apartments              Zeta 1       2.0      2.0   
1            SKA Metro Ville          Eta 2, Eta       2.0      2.0   
2                Prideville    Yamuna Expressway       2.0      2.0   
3      Purvanchal Royal City               Chi 5       4.0      4.0   
4                Stellar One  Greater Noida West       2.0      2.0   

                     builderName       cityName floorSize        floorno  \
0                Paramount Group  Greater Noida    1260               16   
1                      SKA Group  Greater Noida     920    Not available   
2        Imperia Structures Ltd.  Greater Noida     900    Not available   
3  Purvanchal Projects Pvt. Ltd.  Greater Noida    2505               19   
4     Stellar Ventures Pvt. Ltd.  Greater Noida     895    Not available   

  furnshingstatus                                               name  \
0     Unfurnished  2 BHK Apartment for Sale in Golfforeste AC Apa...   
1  Semi-Furnished  2 BHK Apartment for Sale in SKA Metro Ville, E...   
2  Semi-Furnished  2 BHK Apartment for Sale in Prideville , Yamun...   
3  Semi-Furnished  4 BHK Apartment for Sale in Purvanchal Royal C...   
4     Unfurnished  2 BHK Apartment for Sale in Stellar One, Great...   

      price priceInWord propertyType  \
0  3.71e+06    37.1 Lac    Apartment   
1  2.56e+06    25.6 Lac    Apartment   
2  4.68e+06    46.8 Lac    Apartment   
3  1.12e+07     1.12 Cr    Apartment   
4  3.11e+06    31.1 Lac    Apartment   

                                                name  \
0  2 BHK Apartment for Sale in Golfforeste AC Apa...   
1  2 BHK Apartment for Sale in SKA Metro Ville, E...   
2  2 BHK Apartment for Sale in Prideville , Yamun...   
3  4 BHK Apartment for Sale in Purvanchal Royal C...   
4  2 BHK Apartment for Sale in Stellar One, Great...   

                                         description  
0  2 Bath,Unfurnished,16 floor Paramount Golf For...  
1  2 Bath,Semi-Furnished SKA Metro Ville is the f...  
2  2 Bath,Semi-Furnished We at Prideville underst...  
3  4 Bath,Semi-Furnished,19 floor A life where yo...  
4  2 Bath,Unfurnished In Greater Noida(West), alo...

In [150]:
null_values(df_recommend)

Total_values  Null_Count  Percent
Society                   734           0      0.0
locality                  734           0      0.0
bathroom                  734           0      0.0
bedroom                   734           0      0.0
builderName               734           0      0.0
cityName                  734           0      0.0
floorSize                 734           0      0.0
floorno                   734           0      0.0
furnshingstatus           734           0      0.0
name                      734           0      0.0
price                     734           0      0.0
priceInWord               734           0      0.0
propertyType              734           0      0.0
name                      734           0      0.0
description               734           0      0.0

In [ ]:
#df_recommend[df_recommend.Society.isnull()]

In [52]:
df_recommend.columns

Index(['Society', 'locality', 'bathroom', 'bedroom', 'builderName', 'cityName',
       'floorSize', 'floorno', 'furnshingstatus', 'name', 'price',
       'priceInWord', 'propertyType'],
      dtype='object')

In [48]:
col_list=['Society', 'locality', 'bathroom', 'bedroom', 'builderName', 'cityName',
       'floorSize', 'floorno', 'furnshingstatus', 'name', 'price',
       'priceInWord', 'propertyType']

In [ ]:
#del df_recommend['description']

In [59]:
df_recommend['description'] = ''

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [151]:
for col in df_recommend.columns:
    df_recommend['description']=df_recommend['description'].str.cat(df['name'].astype(str), sep =" , ")

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [152]:
df_recommend.head()

Society            locality  bathroom  bedroom  \
0  Golfforeste AC Apartments              Zeta 1       2.0      2.0   
1            SKA Metro Ville          Eta 2, Eta       2.0      2.0   
2                Prideville    Yamuna Expressway       2.0      2.0   
3      Purvanchal Royal City               Chi 5       4.0      4.0   
4                Stellar One  Greater Noida West       2.0      2.0   

                     builderName       cityName floorSize        floorno  \
0                Paramount Group  Greater Noida    1260               16   
1                      SKA Group  Greater Noida     920    Not available   
2        Imperia Structures Ltd.  Greater Noida     900    Not available   
3  Purvanchal Projects Pvt. Ltd.  Greater Noida    2505               19   
4     Stellar Ventures Pvt. Ltd.  Greater Noida     895    Not available   

  furnshingstatus                                               name  \
0     Unfurnished  2 BHK Apartment for Sale in Golfforeste AC Apa...   
1  Semi-Furnished  2 BHK Apartment for Sale in SKA Metro Ville, E...   
2  Semi-Furnished  2 BHK Apartment for Sale in Prideville , Yamun...   
3  Semi-Furnished  4 BHK Apartment for Sale in Purvanchal Royal C...   
4     Unfurnished  2 BHK Apartment for Sale in Stellar One, Great...   

      price priceInWord propertyType  \
0  3.71e+06    37.1 Lac    Apartment   
1  2.56e+06    25.6 Lac    Apartment   
2  4.68e+06    46.8 Lac    Apartment   
3  1.12e+07     1.12 Cr    Apartment   
4  3.11e+06    31.1 Lac    Apartment   

                                                name  \
0  2 BHK Apartment for Sale in Golfforeste AC Apa...   
1  2 BHK Apartment for Sale in SKA Metro Ville, E...   
2  2 BHK Apartment for Sale in Prideville , Yamun...   
3  4 BHK Apartment for Sale in Purvanchal Royal C...   
4  2 BHK Apartment for Sale in Stellar One, Great...   

                                         description  
0  2 Bath,Unfurnished,16 floor Paramount Golf For...  
1  2 Bath,Semi-Furnished SKA Metro Ville is the f...  
2  2 Bath,Semi-Furnished We at Prideville underst...  
3  4 Bath,Semi-Furnished,19 floor A life where yo...  
4  2 Bath,Unfurnished In Greater Noida(West), alo...

In [153]:
df_recommend.description.head(1).T

0    2 Bath,Unfurnished,16 floor Paramount Golf For...
Name: description, dtype: object

In [63]:
tf = TfidfVectorizer(analyzer='word', ngram_range=(1, 3), min_df=0, stop_words='english')

In [67]:
tfidf_matrix = tf.fit_transform(df_recommend['description'])
cosine_similarities = linear_kernel(tfidf_matrix, tfidf_matrix)

In [68]:
tfidf_matrix.data

array([0.22179504, 0.24831057, 0.18668686, ..., 0.08940628, 0.08940628,
       0.08940628])

In [69]:
df_recommend.head(10).T

0  \
Society                                  Golfforeste AC Apartments   
locality                                                    Zeta 1   
bathroom                                                         2   
bedroom                                                          2   
builderName                                        Paramount Group   
cityName                                             Greater Noida   
floorSize                                                   1260     
floorno                                                         16   
furnshingstatus                                        Unfurnished   
name             2 BHK Apartment for Sale in Golfforeste AC Apa...   
price                                                     3.71e+06   
priceInWord                                               37.1 Lac   
propertyType                                             Apartment   
description       Golfforeste AC Apartments Zeta 1 2.0 2.0 Para...   

                                                                 1  \
Society                                            SKA Metro Ville   
locality                                                Eta 2, Eta   
bathroom                                                         2   
bedroom                                                          2   
builderName                                              SKA Group   
cityName                                             Greater Noida   
floorSize                                                    920     
floorno                                              Not available   
furnshingstatus                                     Semi-Furnished   
name             2 BHK Apartment for Sale in SKA Metro Ville, E...   
price                                                     2.56e+06   
priceInWord                                               25.6 Lac   
propertyType                                             Apartment   
description       SKA Metro Ville Eta 2, Eta 2.0 2.0 SKA Group ...   

                                                                 2  \
Society                                                Prideville    
locality                                         Yamuna Expressway   
bathroom                                                         2   
bedroom                                                          2   
builderName                                Imperia Structures Ltd.   
cityName                                             Greater Noida   
floorSize                                                    900     
floorno                                              Not available   
furnshingstatus                                     Semi-Furnished   
name             2 BHK Apartment for Sale in Prideville , Yamun...   
price                                                     4.68e+06   
priceInWord                                               46.8 Lac   
propertyType                                             Apartment   
description       Prideville  Yamuna Expressway 2.0 2.0 Imperia...   

                                                                 3  \
Society                                      Purvanchal Royal City   
locality                                                     Chi 5   
bathroom                                                         4   
bedroom                                                          4   
builderName                          Purvanchal Projects Pvt. Ltd.   
cityName                                             Greater Noida   
floorSize                                                   2505     
floorno                                                         19   
furnshingstatus                                     Semi-Furnished   
name             4 BHK Apartment for Sale in Purvanchal Royal C...   
price                                                     1.12e+07   
priceInWord                                                1.12 Cr   
pr

In [70]:
df_recommend.Society.unique()

array(['Golfforeste AC Apartments', 'SKA Metro Ville', 'Prideville ',
       'Purvanchal Royal City', 'Stellar One', 'Arihant Ambar',
       'ATS Dolce', 'The Halt', 'Sun Twilight', 'Supertech Upcountry',
       'Panchsheel Hynish', 'Gaur Yamuna City', 'Eros Sampoornam I',
       'Gaur Saundaryam', 'SKA Greenarch', 'Sublimis', 'ATS Destinaire',
       'Nirala Greenshire', 'Gaur City', 'Rise Resort Residences',
       'Jaypee Greens Estate Home', 'Meridian Towers', 'Nirala Aspire',
       'Mahagun Mantra 2', 'Paramount Golf Foreste', 'Valencia Homes',
       'Gaur Atulyam', 'Sushant Serene Residency', 'Coco County',
       'Godrej Golf Links', 'AVJ Heights', 'Himalaya Pride',
       'Arihant Abode', 'Plumeria Garden Estate', 'Migsun Ultimo',
       'Supertech Eco Village 3', 'Technocity Apartments',
       'Engineers Enclave', 'Patel Neotown', 'Stellar MI Citi Homes',
       'Supertech Up Country', 'Omaxe Palm Greens', 'Ace Platinum',
       'Express Park view I', 'Migsun Vilaasa',
    

In [77]:
df_recommend[df_recommend.Society=='Shri Radha Sky Garden']

Society         locality  bathroom  bedroom builderName  \
77    Shri Radha Sky Garden  Noida Extension       2.0      2.0  Shri Group   
1355  Shri Radha Sky Garden  Noida Extension       3.0      3.0  Shri Group   
1418  Shri Radha Sky Garden  Noida Extension       3.0      3.0  Shri Group   

           cityName floorSize floorno furnshingstatus  \
77    Greater Noida    1286         8     Unfurnished   
1355  Greater Noida    1874        16     Unfurnished   
1418  Greater Noida    1874         5     Unfurnished   

                                                   name      price  \
77    2 BHK Apartment for Sale in Shri Radha Sky Gar...    4.8e+06   
1355  3 BHK Apartment for Sale in Shri Radha Sky Gar...    5.5e+06   
1418  3 BHK Apartment for Sale in Shri Radha Sky Gar...  5.996e+06   

     priceInWord propertyType  \
77        48 Lac    Apartment   
1355      55 Lac    Apartment   
1418      60 Lac    Apartment   

                                            description  
77     Shri Radha Sky Garden Noida Extension 2.0 2.0...  
1355   Shri Radha Sky Garden Noida Extension 3.0 3.0...  
1418   Shri Radha Sky Garden Noida Extension 3.0 3.0...

In [78]:
df_recommend.columns

Index(['Society', 'locality', 'bathroom', 'bedroom', 'builderName', 'cityName',
       'floorSize', 'floorno', 'furnshingstatus', 'name', 'price',
       'priceInWord', 'propertyType', 'description'],
      dtype='object')

In [88]:
def citybased(city,price=None):
    df_recommend['cityName']=df_recommend['cityName'].str.lower()
    citybase=df_recommend[df_recommend['cityName']==city.lower()]
    citybase=citybase.sort_values(by='price',ascending=True)
    #print(citybase.head())
    if price is not None:
        price=int(price)
        citybase=citybase[citybase.price<=price]
    if(citybase.empty==0):
        pname=citybase[['Society', 'locality', 'bathroom', 'bedroom','floorSize', 'floorno', 'furnshingstatus', 'name', 'price',
                       'priceInWord', 'propertyType']]
        return pname.head(10)
    else:
        print('No Property Available')
   
        
            

In [112]:
def localitybased(locality,price=None):
    df_recommend['locality']=df_recommend['locality'].str.lower()
    localitybase=df_recommend[df_recommend['locality']==locality.lower()]
    localitybase=localitybase.sort_values(by=['bedroom','bathroom','price'],ascending=False)
    #print(citybase.head())
    if price is not None:
        price=int(price)
        localitybase=localitybase[localitybase.price<=price]
    if(localitybase.empty==0):
        pname=localitybase[['Society', 'locality', 'bathroom', 'bedroom','floorSize', 'floorno', 'furnshingstatus', 'name', 'price',
                       'priceInWord', 'propertyType']]
        return pname.head(50)
    else:
        print('No Property Available')

In [106]:
df_recommend.locality.unique()

array(['zeta 1', 'eta 2, eta', 'yamuna expressway', 'chi 5',
       'greater noida west', 'sector-4', 'sector 27', 'sector 1',
       'sector 2', 'pari chowk', 'zeta 2', 'omicron 1', 'noida extention',
       'omicron 3', 'ecotech 3', 'techzone 4', 'sector mu',
       'tech zone, gautam budh nagar, yamuna expressway', 'phi 4',
       'phi 2', 'noida extension', 'chuharpur khadar, sector-chi',
       'sector-zeta', 'omega 1', 'omicron', 'pi 2', 'sector-phi1',
       'sigma 4', 'stellar sigma, sigma 4', 'chi 4', 'tilpata karanwas',
       'chi 2', 'surajpur site -b industrial',
       'surajpur site -c industrial', 'surajpur', 'sector-phi',
       'nri city, omega 2', 'sector 10', 'upsidc site c block h',
       'alpha 1', 'sector-chi', 'chi 3', 'beta 2',
       'sector 143 b, noida express way', 'pi 1 & 2', 'gautam budh nagar',
       'chi-phi', 'sector 3', 'swarnnagari', 'it park, knowledge park 3',
       'gamma 2', 'chamrawali bodaki'], dtype=object)

In [113]:
localitybased('Noida Extention')

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


Society         locality  bathroom  bedroom floorSize  \
401   Supertech Eco Village 3  noida extention       4.0      3.0    1900     
48    Supertech Eco Village 3  noida extention       4.0      3.0       nan   
499   Supertech Eco Village 3  noida extention       3.0      3.0    1255     
324   Supertech Eco Village 3  noida extention       2.0      3.0       nan   
42             Himalaya Pride  noida extention       2.0      3.0    1440     
553   Supertech Eco Village 3  noida extention       2.0      3.0    1300     
666               Laxmi Homes  noida extention       2.0      3.0     900     
653  Gaur City II 10TH Avenue  noida extention       2.0      2.0     990     
517       Amrapali Smart City  noida extention       2.0      2.0     925     
389  Gaur City II 10TH Avenue  noida extention       2.0      2.0     845     
655   Supertech Eco Village 3  noida extention       2.0      2.0     930     
645   Supertech Eco Village 3  noida extention       2.0      2.0     900     
371           Rudra Aqua Casa  noida extention       2.0      2.0    1055     
612   Supertech Eco Village 3  noida extention       2.0      2.0     925     
337   Supertech Eco Village 3  noida extention       2.0      2.0    1021     
345   Supertech Eco Village 3  noida extention       2.0      2.0     925     
111   Supertech Eco Village 3  noida extention       2.0      2.0     925     
148  Gaur City II 10TH Avenue  noida extention       2.0      1.0     555     

           floorno furnshingstatus  \
401              2  Semi-Furnished   
48               2       Furnished   
499             21  Semi-Furnished   
324             15     Unfurnished   
42              12     Unfurnished   
553              6  Semi-Furnished   
666              1  Semi-Furnished   
653             25  Semi-Furnished   
517              6  Semi-Furnished   
389             14  Semi-Furnished   
655              6  Semi-Furnished   
645              3  Semi-Furnished   
371             10  Semi-Furnished   
612             16     Unfurnished   
337             18     Unfurnished   
345             11  Semi-Furnished   
111  Not available     Unfurnished   
148             15  Semi-Furnished   

                                                  name     price priceInWord  \
401  3 BHK Apartment for Sale in Supertech Eco Vill...     1e+07        1 Cr   
48   3 BHK Apartment for Sale in Supertech Eco Vill...  8.15e+06    81.5 Lac   
499  3 BHK Apartment for Sale in Supertech Eco Vill...   4.5e+06      45 Lac   
324  3 BHK Apartment for Sale in Supertech Eco Vill...   5.3e+06      53 Lac   
42   3 BHK Apartment for Sale in Himalaya Pride, No...  5.25e+06    52.5 Lac   
553  3 BHK Apartment for Sale in Supertech Eco Vill...   5.2e+06      52 Lac   
666  3 BHK Apartment for Sale in Laxmi Homes, Noida...   2.8e+06      28 Lac   
653  2 BHK Apartment for Sale in Gaur City II 10TH ...   4.2e+06      42 Lac   
517  2 BHK Apartment for Sale in Amrapali Smart Cit...     4e+06      40 Lac   
389  2 BHK Apartment for Sale in Gaur City II 10TH ...   3.9e+06      39 Lac   
655  2 BHK Apartment for Sale in Supertech Eco Vill...   3.8e+06      38 Lac   
645  2 BHK Apartment for Sale in Supertech Eco Vill...   3.6e+06      36 Lac   
371  2 BHK Apartment for Sale in Rudra Aqua Casa, N...   3.5e+06      35 Lac   
612  2 BHK Apartment for Sale in Supertech Eco Vill...   3.5e+06      35 Lac   
337  2 BHK Apartment for Sale in Supertech Eco Vill...   3.3e+06      33 Lac   
345  2 BHK Apartment for Sale in Supertech Eco Vill...   3.3e+06      33 Lac   
111  2 BHK Builder Floor Apartment for Sale in Supe...   2.9e+06      29 Lac   
148  1 BHK Apartment for Sale in Gaur City II 10TH ...   2.2e+06      22 Lac   

                propertyType  
401                Apartment  
48                 Apartment  
499                Apartment  
324                Apartment  
42                 Apartment  
553                Apartment  
666                Apartment  
653                Apartment

In [90]:
citybased('Greater Noida')

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


Society           locality  bathroom  bedroom  \
1404  Yamuna Expressway Authority Plot  Yamuna Expressway       1.0      1.0   
576   Yamuna Expressway Authority Plot  Yamuna Expressway       1.0      1.0   
311                    Authority Plots  Yamuna Expressway       1.0      1.0   
1537               Supertech Upcountry  Yamuna Expressway       1.0      1.0   
1267                           Chi Phi            Chi-Phi       1.0      1.0   
35                        Gaur Atulyam          Omicron 1       1.0      1.0   
1338                      Lotus Villas    Noida Extension       1.0      1.0   
1342                      Lotus Villas    Noida Extension       1.0      1.0   
197                       Lotus Villas    Noida Extension       1.0      1.0   
464                    Ajnara Panorama  Yamuna Expressway       1.0      1.0   

     floorSize floorno furnshingstatus  \
1404     410         1     Unfurnished   
576       40         2  Semi-Furnished   
311       30         3  Semi-Furnished   
1537     600         1  Semi-Furnished   
1267      30    Ground     Unfurnished   
35       500         2     Unfurnished   
1338     650         1  Semi-Furnished   
1342     650    Ground  Semi-Furnished   
197      650    Ground  Semi-Furnished   
464      515        28     Unfurnished   

                                                   name     price priceInWord  \
1404  1 BHK Apartment for Sale in Yamuna Expressway ...   1.2e+06      12 Lac   
576   1 BHK Apartment for Sale in Yamuna Expressway ...  1.25e+06    12.5 Lac   
311   1 BHK Apartment for Sale in Authority Plots, Y...  1.25e+06    12.5 Lac   
1537  1 BHK Apartment for Sale in Supertech Upcountr...  1.43e+06    14.3 Lac   
1267       1 BHK Apartment for Sale in Chi Phi, Chi-Phi   1.5e+06      15 Lac   
35    1 BHK Apartment for Sale in Gaur Atulyam, Omic...   1.6e+06      16 Lac   
1338  1 BHK Builder Floor Apartment for Sale in Lotu...   1.7e+06      17 Lac   
1342  1 BHK Builder Floor Apartment for Sale in Lotu...   1.8e+06      18 Lac   
197   1 BHK Apartment for Sale in Lotus Villas, Noid...  1.81e+06    18.1 Lac   
464   1 BHK Apartment for Sale in Ajnara Panorama, Y...  1.85e+06    18.5 Lac   

                 propertyType  
1404                Apartment  
576                 Apartment  
311                 Apartment  
1537                Apartment  
1267                Apartment  
35                  Apartment  
1338  Builder Floor Apartment  
1342  Builder Floor Apartment  
197                 Apartment  
464                 Apartment

In [162]:
def requirementbased(city, price=None,*features):
    price=int(price)
    df_recommend['cityName']=df_recommend['cityName'].str.lower()
    #df_recommend['locality']=df_recommend['locality'].str.lower()
    features = ''.join(features)
    features=features.lower()
    features_tokens=word_tokenize(features)
    sw=stopwords.words('english')
    description_matrix = tf.fit_transform(df_recommend[features])
    #cosine_similarities = linear_kernel(tfidf_matrix, tfidf_matrix)
    lemm=WordNetLemmatizer()
    f1_set = {w for w in features_tokens if not w in sw}
    f_set=set()
    for se in f1_set:
        f_set.add(lemm.lemmatize(se))
        print(f_set)
    reqbased=df_recommend[df_recommend['cityName']==city.lower()]
    if price!= None:
        reqbased=reqbased[reqbased['price'] <=price]
    reqbased=reqbased.set_index(np.arange(reqbased.shape[0]))
    l1 =[];l2 =[];cos=[];
    #print(reqbased['description'])
    for i in range(reqbased.shape[0]):
        temp_tokens=word_tokenize(reqbased['description'][i])
        temp1_set={w for w in temp_tokens if not w in sw}
        temp_set=set()
        for se in temp1_set:
            temp_set.add(lemm.lemmatize(se))
            print(temp_set)
        rvector = temp_set.intersection(f_set)
        #print(rvector)
        cos.append(len(rvector))
    reqbased['similarity']=cos
    reqbased=reqbased.sort_values(by='similarity',ascending=False)
    return reqbased[['Society', 'locality', 'bathroom', 'bedroom','floorSize', 'floorno', 'furnshingstatus', 'name', 'price',
                       'priceInWord', 'propertyType','similarity']]

In [163]:
df_recommend.cityName.unique()

array(['greater noida'], dtype=object)

In [166]:
requirementbased('Greater Noida',8000000,"I want 3 bedroom with minimum 1400 sqft apartment in Noida-Extension")

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


{'sqft'}
{'want', 'sqft'}
{'want', 'sqft', 'apartment'}
{'want', 'noida-extension', 'sqft', 'apartment'}
{'sqft', 'want', 'apartment', 'noida-extension', 'bedroom'}
{'sqft', 'want', 'apartment', 'noida-extension', 'bedroom', '3'}
{'sqft', 'want', 'apartment', 'noida-extension', 'bedroom', '3', '1400'}
{'sqft', 'want', 'apartment', 'noida-extension', 'bedroom', '3', '1400', 'minimum'}
{'complimented'}
{'complimented', 'Greater'}
{'complimented', 'Group', 'Greater'}
{'complimented', 'Group', 'Greater', '2.0'}
{'complimented', 'Greater', 'Group', '2.0', 'healthy'}
{'complimented', 'Greater', 'Group', '2.0', 'healthy', '1260'}
{'complimented', 'Greater', 'Group', '2.0', 'healthy', '1260', 'family'}
{'complimented', 'Greater', '16', 'Group', '2.0', 'healthy', '1260', 'family'}
{'complimented', 'Paramount', 'Greater', '16', 'Group', '2.0', 'healthy', '1260', 'family'}
{'complimented', 'Paramount', 'Noida', 'Greater', '16', 'Group', '2.0', 'healthy', '1260', 'family'}
{'complimented', 'Paramo

{'housing'}
{'housing', 'Greater'}
{'residential', 'housing', 'Greater'}
{'residential', 'Metro', 'housing', 'Greater'}
{'housing', 'Greater', 'residential', 'Metro', '33.2'}
{'housing', 'Greater', 'overall', 'residential', 'Metro', '33.2'}
{'housing', 'Greater', 'overall', 'interior', 'residential', 'Metro', '33.2'}
{'housing', 'Greater', 'overall', 'interior', 'residential', 'ApartmentsDesigned', 'Metro', '33.2'}
{'housing', 'Greater', 'overall', 'interior', 'residential', 'ApartmentsDesigned', '3', 'Metro', '33.2'}
{'housing', 'Greater', 'overall', 'interior', 'residential', 'ApartmentsDesigned', '3', 'Metro', 'resulting', '33.2'}
{'housing', 'Greater', 'overall', 'interior', 'residential', 'ApartmentsDesigned', '3', 'Metro', 'resulting', 'fresh', '33.2'}
{'housing', 'Greater', 'overall', 'interior', 'residential', 'IGBC', 'ApartmentsDesigned', '3', 'Metro', 'resulting', 'fresh', '33.2'}
{'housing', 'Greater', 'overall', 'interior', 'residential', 'IGBC', '1062', 'ApartmentsDesigned

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'Greater', 'In', 'face', 'Tiles', 'Leasehold', 'Ceramic', '3600000.0', 'house', 'It', 'Noida', 'Centre', '17th', 'located', 'Sale', 'place', 'Housing', '36', 'Additional', 'Multistorey', 'part', 'Institute', 'Semi-Furnished,17', 'overlook', 'available', 'Room', 'BHK', 'Flooring', 'easily', 'breathing', '1', '1060', ')', 'Education', 'Indian', 'Eros', 'International', 'Lac', 'maximum', 'And', 'provides', 'floor', 'Apartment', '.', 'Aids', 'Sampoornam', 'East', 'Bath', 'Hospital', 'Other', 'key', 'facing', 'km', 'cover', 'Development'}
{'Greater', 'In', 'face', 'Tiles', 'Leasehold', 'Ceramic', '3600000.0', 'house', 'It', 'Noida', 'Centre', '17th', 'located', 'Sale', 'place', 'Housing', '36', 'Additional', 'Multistorey', 'part', 'Institute', 'Semi-Furnished,17', 'overlook', 'available', 'Room', 'BHK', 'Flooring', '17', 'easily', 'breathing', '1', '1060', ')', 'Education', 'Indian', 'Eros', 'International', 'Lac', 'maximum', 'And', 'provides', 'floor', 'Apartment', '.', 'Aids', 'Sampoorna

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




{'Noida', 'nan', 'ventilation', 'Greater', 'car', 'open', '3.0', 'Group', 'It'}
{'Noida', 'nan', 'ventilation', 'Greater', 'car', 'open', 'corner', '3.0', 'Group', 'It'}
{'Noida', 'nan', 'ventilation', 'Greater', 'car', 'open', 'corner', '3.0', 'Group', 'Sale', 'It'}
{'Noida', 'nan', 'ventilation', 'Greater', 'car', 'open', 'corner', '3.0', 'Semi-Furnished', 'Group', 'Sale', 'It'}
{'Noida', 'nan', 'ventilation', 'Greater', 'car', 'open', 'corner', '3.0', 'Semi-Furnished', 'two', 'Group', 'Sale', 'It'}
{'Noida', 'nan', 'ventilation', 'Greater', 'car', 'open', 'corner', '3.0', 'Semi-Furnished', 'two', 'City', 'Group', 'Sale', 'It'}
{'Noida', 'nan', 'ventilation', 'Greater', 'car', 'open', 'corner', '3.0', 'Semi-Furnished', 'two', 'City', 'Group', '3', 'Sale', 'It'}
{'Noida', 'nan', 'ventilation', 'Greater', 'car', 'open', 'corner', '3.0', 'Semi-Furnished', 'two', 'City', 'side', 'Group', '3', 'Sale', 'It'}
{'Noida', 'nan', 'ventilation', 'Greater', 'car', 'open', 'corner', '3.0', 'Semi-

{'1st', 'amount', 'happiness.Ideally', 'Greater', 'system', 'grab', 'residential', 'lead', 'park', 'clock', 'prominent', 'essential', 'royal', 'east', 'built', 'market', 'vitrified', 'Ajnara', 'kitchen.Both', 'Aster', 'kitchen', 'ambience', 'swimming', 'norm', 'apparel', 'house', 'Greenaria', 'covered', '24-storey', 'Spanning', 'fan', 'located', 'overall', '...', 'keep', 'prime', 'attached', 'wardrobe', '3', '12', '!', 'semi-furnished', 'valuable', 'ample', 'West', 'full', 'named', 'main', 'entire', 'gymnasium', 'electrical', 'brilliantly', 'kid', 'Ltd', 'bedroom', 'pool', 'world-class', 'The', 'close', 'arrange', 'taxi', 'Lac', 'Of', 'connection', 'across', 'track', 'renowned', 'lifestyle', '2nd', 'living', 'planned', 'centre', 'facing', '&'}
{'1st', 'amount', 'happiness.Ideally', 'Greater', 'system', 'grab', 'residential', 'lead', 'park', 'clock', 'prominent', 'essential', 'royal', 'east', 'built', 'market', 'vitrified', 'Ajnara', 'kitchen.Both', 'Aster', 'kitchen', 'ambience', 'swim

{'heart', '38', 'Sikka', '1315', 'Greater', '3.0', 'going', 'city', 'Not', 'KAAMYA', 'Group', 'air-conditioned', '2.0', 'project', 'Greens', 'environment', 'Noida', 'open', 'located', 'bright', 'Semi-Furnished', 'become', 'Kaamya', 'nearly', 'free', 'Life', 'pocket', '3', 'Indeed', 'hold', 'every', 'destination', 'luxuriously', 'SIKKA', 'available', 'West', 'BHK', 'suit', 'like', 'everyone', 'well', 'amenity', 'offer', 'facility', 'GREENS'}
{'heart', '38', 'Sikka', '1315', 'Greater', '3.0', 'going', 'city', 'Not', 'KAAMYA', 'Group', 'air-conditioned', '2.0', 'project', 'Greens', 'environment', 'Noida', 'open', 'located', 'bright', 'Semi-Furnished', 'become', 'Kaamya', 'nearly', 'free', 'Life', 'pocket', '3', 'Indeed', 'hold', 'every', 'destination', 'luxuriously', 'SIKKA', 'available', 'West', 'BHK', 'suit', 'like', 'everyone', 'well', 'pollution', 'amenity', 'offer', 'facility', 'GREENS'}
{'heart', '38', 'Sikka', '1315', 'Greater', '3.0', 'going', 'city', 'Not', 'KAAMYA', 'Group', 'ai

Society                      locality  bathroom  \
561          Purvanchal Royal City                         Chi 5       3.0   
46                     Vrinda City                         Phi 4       2.0   
67                   Raksha Addela            Greater Noida West       2.0   
251                  NRI Residency                    Pari Chowk       2.0   
58                     Czar Suites                       Omicron       2.0   
590                 Valencia Homes                      Sector 1       2.0   
42             Express Park view I             Yamuna Expressway       3.0   
529                      Gaur City            Greater Noida West       3.0   
383              Omaxe Palm Greens                     Sector MU       2.0   
59                 Unitech Cascade                          PI 2       2.0   
568         Plumeria Garden Estate                       Omicron       3.0   
511               Ajnara Le Garden            Greater Noida West       2.0   
606                       The Halt                      Sector-4       1.0   
54     Nimbus Express Park View II  Chuharpur Khadar, Sector-Chi       2.0   
95                 Super MIG Flats                     Omicron 3       2.0   
57                Mahagun Mantra 1            Greater Noida West       3.0   
552                     ATS Allure             Yamuna Expressway       2.0   
257                Unitech Horizon                          PI 2       3.0   
571                 Stellar Jeevan                      Sector 1       4.0   
94         Shri Radha Aqua Gardens            Greater Noida West       2.0   
479           Gaur City 5th Avenue               Noida Extension       2.0   
64               Nirala Greenshire            Greater Noida West       2.0   
565                  Arihant Ambar            Greater Noida West       2.0   
152              Nirala Greenshire            Greater Noida West       2.0   
603                  Arihant Ambar            Greater Noida West       2.0   
263        Mahaluxmi Green Mansion                        Zeta 1       2.0   
169              Omaxe Palm Greens                     Sector MU       3.0   
281  Eldeco Residency Green Medows                    Sector-Phi       3.0   
73         Supertech Eco Village 3               Noida Extention       2.0   
74               Nirala Greenshire            Greater Noida West       4.0   
..                             ...                           ...       ...   
271             DPL Flora Heritage                      Sector 1       2.0   
270                    AVJ Heights                        Zeta 1       1.0   
264              Eros Sampoornam I                      Sector 2       2.0   
261        Mahaluxmi Green Mansion                        Zeta 1       2.0   
260       Sushant Serene Residency                    Eta 2, Eta       2.0   
259          Assotech Springfields                        Zeta 1       4.0   
300            Supertech Upcountry             Yamuna Expressway       1.0   
303                      Gaur City            Greater Noida West       2.0   
336                    Earth Towne                      Sector 1       2.0   
305            Amrapali Smart City               Noida Extention       2.0   
335            Express Park view I             Yamuna Expressway       1.0   
333                      ATS Dolce                        Zeta 1       2.0   
332                 Shivalik Homes                      Surajpur       2.0   
331                RG Luxury Homes            Greater Noida West       2.0   
328                    Czar Suites                     Omicron 1       1.0   
327                      Casagrand                    Sector-Chi       2.0   
326        Mahaluxmi Green Mansion                        Zeta 1       2.0   
324          Gaur City  7th Avenue               Noida Extension       2.0   
323                  Nirala Estate               Noida Extension       2.0   
322            Airwil Green Avenue               

In [174]:
print(df_recommend[df_recommend.locality=='Noida Extension'].description[:1])

77    2 Bath,Unfurnished,8 floor  This Multistorey A...
Name: description, dtype: object


In [ ]:
def requirementbased(city,number,features):
    hotel['city']=hotel['city'].str.lower()
    hotel['roomamenities']=hotel['roomamenities'].str.lower()
    features=features.lower()
    features_tokens=word_tokenize(features)  
    sw = stopwords.words('english')
    lemm = WordNetLemmatizer()
    f1_set = {w for w in features_tokens if not w in sw}
    f_set=set()
    for se in f1_set:
        f_set.add(lemm.lemmatize(se))
    reqbased=hotel[hotel['city']==city.lower()]
    reqbased=reqbased[reqbased['guests_no']==number]
    reqbased=reqbased.set_index(np.arange(reqbased.shape[0]))
    l1 =[];l2 =[];cos=[];
    #print(reqbased['roomamenities'])
    for i in range(reqbased.shape[0]):
        temp_tokens=word_tokenize(reqbased['roomamenities'][i])
        temp1_set={w for w in temp_tokens if not w in sw}
        temp_set=set()
        for se in temp1_set:
            temp_set.add(lemm.lemmatize(se))
        rvector = temp_set.intersection(f_set)
        #print(rvector)
        cos.append(len(rvector))
    reqbased['similarity']=cos
    reqbased=reqbased.sort_values(by='similarity',ascending=False)
    reqbased.drop_duplicates(subset='hotelcode',keep='first',inplace=True)
    return reqbased[['hotelname','roomtype','guests_no','starrating','address','roomamenities','ratedescription','similarity']].head(10)